In [ ]:
import os
import random
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
plt.style.use("ggplot")
%matplotlib inline

from tqdm import tqdm_notebook, tnrange
from itertools import chain
from skimage.io import imread, imshow, concatenate_images
from skimage.transform import resize
from skimage.morphology import label
from sklearn.model_selection import train_test_split
import tensorflow as tf
from keras import layers
from keras.models import Model, load_model
from keras.layers import Input, BatchNormalization, Activation, Dense, Dropout
from keras.layers.core import Lambda, RepeatVector, Reshape
from keras.layers.convolutional import Conv2D, Conv2DTranspose
from keras.layers.pooling import MaxPooling2D, GlobalMaxPool2D
from keras.layers import concatenate, add, Add
from keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.preprocessing.image import ImageDataGenerator, array_to_img, img_to_array, load_img

In [ ]:
# Set some parameters
im_width = 128
im_height = 128
border = 5

In [ ]:
ids = next(os.walk("/kaggle/input/duts-salient-object-detection-dataset/DUTS-TR/DUTS-TR-Image"))[2] # list of names all images in the given path
# ids = next(os.walk("/kaggle/input/duts-salient-object-detection-dataset/DUTS-TE/DUTS-TE-Image"))[2] # list of names all images in the given path
print("No. of images = ", len(ids))

In [ ]:
X = np.zeros((len(ids), im_height, im_width, 1), dtype=np.float32)
y = np.zeros((len(ids), im_height, im_width, 1), dtype=np.float32)

#### Load the images and masks into arrays

In [ ]:
from tqdm.notebook import tqdm

# tqdm is used to display the progress bar
for n, id_ in tqdm(enumerate(ids), total=len(ids)):
    # Load images
#     img = load_img("/kaggle/input/duts-salient-object-detection-dataset/DUTS-TR/DUTS-TR-Image/"+id_, grayscale=True)  
    img = load_img("/kaggle/input/duts-salient-object-detection-dataset/DUTS-TR/DUTS-TR-Image/"+id_, color_mode = "grayscale")
#     img = load_img("/kaggle/input/duts-salient-object-detection-dataset/DUTS-TE/DUTS-TE-Image"+id_, color_mode = "grayscale")

    x_img = img_to_array(img)
    x_img = resize(x_img, (im_width, im_width, 1), mode = 'constant', preserve_range = True)
    # Load masks
    mask = img_to_array(load_img("/kaggle/input/duts-salient-object-detection-dataset/DUTS-TR/DUTS-TR-Mask/"+id_.split('.')[0]+'.png', grayscale=True))
#     mask = img_to_array(load_img("/kaggle/input/duts-salient-object-detection-dataset/DUTS-TE/DUTS-TE-Mask"+id_.split('.')[0]+'.png', grayscale=True))

    mask = resize(mask, (im_width, im_width, 1), mode = 'constant', preserve_range = True)
    # Save imagesdvdvd
    X[n] = x_img/255.0
    y[n] = mask/255.0

In [ ]:
X = np.load('/kaggle/input/dutomron/DUT-OMRON-img.npy')
y = np.load('/kaggle/input/dutomron/DUT-OMRON-mask.npy')

In [ ]:
# Split train and valid
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.1, random_state=42)

In [ ]:
print('Train Images: ',len(X_train), ' Train Labels: ',len(y_train))
print('Test Images: ',len(X_valid), ' Test Labels: ',len(y_valid))

In [ ]:
plt.imshow(X_train[0])

#### Below code can be used to visualize the images and corresponding masks

In [ ]:
import random
# Visualize any randome image along with the mask
ix = random.randint(0, len(X_train))
has_mask = y_train[ix].max() > 0 # salt indicator

fig, (ax1, ax2) = plt.subplots(1, 2, figsize = (20, 15))

ax1.imshow(X_train[ix, ..., 0], cmap = 'gray')
if has_mask: # if Groundtruth
    # draw a boundary(contour) in the original image separating salt and non-salt areas
    ax1.contour(y_train[ix].squeeze(), colors = 'k', linewidths = 5, levels = [0.5])
ax1.set_title('Image')

ax2.imshow(y_train[ix].squeeze(), cmap = 'gray')
ax2.set_title('Ground truth')

In [ ]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers 
from tensorflow.keras.layers import Input , Conv2D , MaxPooling2D , Dropout , concatenate , UpSampling2D, BatchNormalization, Activation, Add, Dense, LSTM, add
from tensorflow.keras import models
from tensorflow.keras import losses
from tensorflow.keras import optimizers
import numpy as np
from tensorflow.keras import backend as K
from tensorflow.keras.metrics import Recall, Precision

In [ ]:
################Residual Block ##############################
def BatchActivate(x):
    x = BatchNormalization()(x)
    x = Activation('relu')(x)
    return x

def convolution_block(x, filters, size, strides=(1,1), padding='same', activation=True):
    x = Conv2D(filters, size, strides=strides, padding=padding)(x)
    if activation == True:
        x = BatchActivate(x)
    return x

def residual_block(blockInput, num_filters, batch_activate = False):
    x = BatchActivate(blockInput)
    x = convolution_block(x, num_filters, (3,3) )
    x = convolution_block(x, num_filters, (3,3), activation=False)
    x = Add()([x, blockInput])
    if batch_activate:
        x = BatchActivate(x)
    return x
#################End Residual Block##############################

In [ ]:
#################ASPP Module#####################################
def convolution_blockspp(
    block_input,
    num_filters=256,
    kernel_size=3,
    dilation_rate=1,
    padding="same",
    use_bias=False,
):
    x = layers.Conv2D(
        num_filters,
        kernel_size=kernel_size,
        dilation_rate=dilation_rate,
        padding="same",
        use_bias=use_bias,
        kernel_initializer=keras.initializers.HeNormal(),
    )(block_input)
    x = layers.BatchNormalization()(x)
    return tf.nn.relu(x)


def DilatedSpatialPyramidPooling(dspp_input):
    dims = dspp_input.shape
    x = layers.AveragePooling2D(pool_size=(dims[-3], dims[-2]))(dspp_input)
    x = convolution_blockspp(x, kernel_size=1, use_bias=True)
    out_pool = layers.UpSampling2D(
        size=(dims[-3] // x.shape[1], dims[-2] // x.shape[2]), interpolation="bilinear",
    )(x)

    out_1 = convolution_blockspp(dspp_input, kernel_size=1, dilation_rate=1)
    out_6 = convolution_blockspp(dspp_input, kernel_size=3, dilation_rate=6)
    out_12 = convolution_blockspp(dspp_input, kernel_size=3, dilation_rate=12)
    out_18 = convolution_blockspp(dspp_input, kernel_size=3, dilation_rate=18)

    x = layers.Concatenate(axis=-1)([out_pool, out_1, out_6, out_12, out_18])
    output = convolution_blockspp(x, kernel_size=1)
    return output
#################End ASPP Block#############################

In [ ]:
import tensorflow as tf

# def conv2d_block(inputs, filters, kernel_size=3, strides=1, use_bn=True):
#     x = tf.keras.layers.Conv2D(filters, kernel_size, strides=strides, padding='same')(inputs)
#     if use_bn:
#         x = tf.keras.layers.BatchNormalization()(x)
#     x = tf.keras.layers.ReLU()(x)
#     return x
def conv2d_block(input_tensor, n_filters, kernel_size = 3, batchnorm = True):
    """Function to add 2 convolutional layers with the parameters passed to it"""
    # first layer
    x = Conv2D(filters=n_filters, kernel_size=(kernel_size, kernel_size), kernel_initializer="he_normal",
               padding="same")(input_tensor)
    if batchnorm:
        x = BatchNormalization()(x)
    x = Activation("relu")(x)

    # second layer
    x = Conv2D(filters=n_filters, kernel_size=(kernel_size, kernel_size), kernel_initializer="he_normal",
               padding="same")(x)
    if batchnorm:
        x = BatchNormalization()(x)
    x = Activation("relu")(x)

    return x

def get_unet(input_img, n_filters = 16, dropout = 0.1, batchnorm = True):
    """Function to define the UNET Model"""
    # Contracting Path
    c1 = conv2d_block(input_img, n_filters * 1, kernel_size = 3, batchnorm = batchnorm)
    r1 = residual_block(c1, n_filters * 1)
    p1 = MaxPooling2D((2, 2))(r1)
    p1 = Dropout(dropout)(p1)
    
    c2 = conv2d_block(p1, n_filters * 2, kernel_size = 3, batchnorm = batchnorm)
    r2 = residual_block(c2, n_filters * 2)
    p2 = MaxPooling2D((2, 2))(c2)
    p2 = Dropout(dropout)(p2)
    
    c3 = conv2d_block(p2, n_filters * 4, kernel_size = 3, batchnorm = batchnorm)
    r3 = residual_block(c3, n_filters * 4)
    p3 = MaxPooling2D((2, 2))(c3)
    p3 = Dropout(dropout)(p3)
    
    c4 = conv2d_block(p3, n_filters * 8, kernel_size = 3, batchnorm = batchnorm)
    r4 = residual_block(c4, n_filters * 8)
    p4 = MaxPooling2D((2, 2))(c4)
    p4 = Dropout(dropout)(p4)
    
    c5 = conv2d_block(p4, n_filters = n_filters * 16, kernel_size = 3, batchnorm = batchnorm)
    
    # Expansive Path
    u6 = Conv2DTranspose(n_filters * 8, (3, 3), strides = (2, 2), padding = 'same')(c5)
    u6 = concatenate([u6, c4])
    u6 = Dropout(dropout)(u6)
    c6 = conv2d_block(u6, n_filters * 8, kernel_size = 3, batchnorm = batchnorm)
    
    u7 = Conv2DTranspose(n_filters * 4, (3, 3), strides = (2, 2), padding = 'same')(c6)
    u7 = concatenate([u7, c3])
    u7 = Dropout(dropout)(u7)
    c7 = conv2d_block(u7, n_filters * 4, kernel_size = 3, batchnorm = batchnorm)
    
    u8 = Conv2DTranspose(n_filters * 2, (3, 3), strides = (2, 2), padding = 'same')(c7)
    u8 = concatenate([u8, c2])
    u8 = Dropout(dropout)(u8)
    c8 = conv2d_block(u8, n_filters * 2, kernel_size = 3, batchnorm = batchnorm)
    
    u9 = Conv2DTranspose(n_filters * 1, (3, 3), strides = (2, 2), padding = 'same')(c8)
    u9 = concatenate([u9, c1])
    u9 = Dropout(dropout)(u9)
    c9 = conv2d_block(u9, n_filters * 1, kernel_size = 3, batchnorm = batchnorm)
    
    outputs = Conv2D(1, (1, 1), activation='sigmoid')(c9)
    model = Model(inputs=[input_img], outputs=[outputs])
    return model

In [ ]:
def jaccard(y_true, y_pred, smooth=1):
  intersection = K.sum(K.abs(y_true * y_pred), axis=[1,2,3])
  union = K.sum(y_true,[1,2,3])+K.sum(y_pred,[1,2,3])-intersection
  iou = K.mean((intersection + smooth) / (union + smooth), axis=0)
  return iou

In [ ]:
input_img = Input((im_height, im_width, 1), name='img')
model = get_unet(input_img, n_filters=16, dropout=0.05, batchnorm=True)
model.compile(optimizer=Adam(), loss="binary_crossentropy", metrics=["accuracy","mae",jaccard,keras.metrics.Precision(),keras.metrics.Recall()])

In [ ]:
model.summary()

In [ ]:
callbacks = [
    EarlyStopping(patience=500, verbose=1),
    ReduceLROnPlateau(factor=0.1, patience=5, min_lr=0.0001, verbose=1),
    ModelCheckpoint('/kaggle/working/saliency.h5', verbose=1, save_best_only=True, save_weights_only=True)
]

In [ ]:
# results = model.fit(X_train, y_train, batch_size=16, epochs=100, callbacks=callbacks,\
#                     validation_data=(X_valid, y_valid))
results = model.fit(X_train, y_train, batch_size=16, epochs=10, callbacks=callbacks,\
                    validation_data=(X_valid, y_valid))

In [ ]:
plt.figure(figsize=(8, 8))
plt.title("Learning curve")
plt.plot(results.history["loss"], label="loss")
plt.plot(results.history["val_loss"], label="val_loss")
plt.plot( np.argmin(results.history["val_loss"]), np.min(results.history["val_loss"]), marker="x", color="r", label="best model")
plt.xlabel("Epochs")
plt.ylabel("log_loss")
plt.legend();

### Inference

In [ ]:
# load the best model
model.load_weights('/kaggle/working/saliency.h5')

In [ ]:
# Evaluate on validation set (this must be equals to the best log_loss)
model.evaluate(X_valid, y_valid, verbose=1)

In [ ]:
# Predict on train, val and test
preds_train = model.predict(X_train, verbose=1)
preds_val = model.predict(X_valid, verbose=1)

In [ ]:
# Threshold predictions
preds_train_t = (preds_train > 0.5).astype(np.uint8)
preds_val_t = (preds_val > 0.5).astype(np.uint8)

In [ ]:
def plot_sample(X, y, preds, binary_preds, ix=None):
    """Function to plot the results"""
    if ix is None:
        ix = random.randint(0, len(X))

    has_mask = y[ix].max() > 0

    fig, ax = plt.subplots(1, 4, figsize=(20, 10))
    ax[0].imshow(X[ix, ..., 0], cmap='gray')
    if has_mask:
        ax[0].contour(y[ix].squeeze(), colors='k', levels=[0.5])
    ax[0].set_title('Object')

    ax[1].imshow(y[ix].squeeze())
    ax[1].set_title('Actual Object')

    ax[2].imshow(preds[ix].squeeze(), vmin=0, vmax=1)
    if has_mask:
        ax[2].contour(y[ix].squeeze(), colors='k', levels=[0.5])
    ax[2].set_title('Predicted Object')
    
    ax[3].imshow(binary_preds[ix].squeeze(), vmin=0, vmax=1)
    if has_mask:
        ax[3].contour(y[ix].squeeze(), colors='k', levels=[0.5])
    ax[3].set_title('Object Predicted binary');

### Predictions on training set

In [ ]:
# Check if training data looks all right
plot_sample(X_train, y_train, preds_train, preds_train_t, ix=14)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

In [ ]:
plot_sample(X_train, y_train, preds_train, preds_train_t)

### Predictions on test set

In [ ]:
# Check if valid data looks all right
plot_sample(X_valid, y_valid, preds_val, preds_val_t, ix=19)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)

In [ ]:
plot_sample(X_valid, y_valid, preds_val, preds_val_t)